In [1]:
import sys
sys.path += ['..']

from data_collection.data_collection import LoggerSet, Logger

import numpy as np
import pandas as pd
import plotly.express as px
from data_collection.video_data import get_frame_iterator
from pathlib import Path
from typing import Iterable, Tuple, List
from tqdm import tqdm
import datetime
import tensorflow as tf
import tensorflow.keras as keras

%load_ext autoreload
%autoreload 2


2024-06-11 20:23:13.649600: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-11 20:23:14.290411: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


# Note
- Condition: same as test 6 but with augmentation
- output L/R PWM - with smoothing - 50 steps
- Also added speed as an input - no smoothing needed for speed
- too much augmentation destoryed the result

# Loading data 

In [2]:
from with_linear_acc import Session
sessions = Session.load_multiple_session('./data')
frames, df = Session.concatenate_multiple_sessions(sessions)

[mov,mp4,m4a,3gp,3g2,mj2 @ 0x556c1904bbc0] moov atom not found


## Inspection only

In [3]:
df = sessions[0].data['angular_speed_control_df']

In [4]:

def mean_nominmax(x):
    return (x.sum()-x.max()-x.min())/(len(x)-2)
asd0 = df['angular_velocity'].rolling(100).apply(mean_nominmax).shift(-99)

asd = df['angular_velocity'].rolling(50).apply(mean_nominmax).shift(-49)
asd1 = df['angular_velocity'].rolling(3).apply(mean_nominmax).shift(-2)


px.line(y=[asd1, asd, asd0])

# Select data for the model

In [3]:
def prepare_to_tensorflow(frames, df):

    # data selection
    df = df.query('speed!=0')

    # match the data with the frame
    frame2data = df.groupby('exact_total_frame_idx')[['linacc0', 'linacc1', 'linacc2', 'speed']].mean()
    outputs = df.groupby('offset_total_frame_idx')[['left_smooth', 'right_smooth']].mean()

    # the reindexed data
    frame_indices = outputs.index.values

    frames_reindexed = frames[frame_indices]
    other_inputs = frame2data.reindex(frame_indices)

    # screen out the nans
    nafilter = (~other_inputs.isna().any(axis=1)).values

    frames_reindexed = frames_reindexed[nafilter]
    other_inputs = other_inputs.values[nafilter]
    outputs = outputs.values[nafilter]
    
    
    return frames_reindexed, other_inputs/10, outputs/100

In [4]:
frames_in, other_in, out = prepare_to_tensorflow(frames, df)

In [5]:

from train_tools import validation_chunk_split

In [6]:
train_idx, val_idx = validation_chunk_split(len(frames_in), val_split=0.2)
train_frames, train_other, train_out = frames_in[train_idx], other_in[train_idx], out[train_idx]
val_frames, val_other, val_out = frames_in[val_idx], other_in[val_idx], out[val_idx]

# Model

In [7]:
def get_model(lr=.1, other_metrics=[]):
    tf.keras.backend.clear_session()
    image_shape = 64, 114, 3

    img_aug_preprocess_layers = [
        keras.layers.RandomTranslation(0.05, 0.05, fill_mode='reflect'),
        keras.layers.RandomRotation(0.02, fill_mode='reflect'),
        keras.layers.RandomZoom(0.05, fill_mode='reflect'),
        keras.layers.RandomContrast(0.5),
        keras.layers.RandomBrightness([-0.7, 0.7])
    ]
    
    cnn_layers =  [
        keras.layers.Conv2D(16, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(32, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(64, 5, strides=2, activation='relu'),         
        keras.layers.Conv2D(64, 3, activation='relu'), 
        keras.layers.Conv2D(96, 3, activation='relu'),         
        keras.layers.Flatten(),
        keras.layers.Dropout(0.2),
    ]
    
    cnn = keras.Sequential(
        [
            keras.layers.InputLayer(image_shape),
            keras.layers.Rescaling(1/255), 
            *img_aug_preprocess_layers,
            *cnn_layers
        ])

    other_inputs = keras.layers.InputLayer((4,))
    x = keras.layers.Concatenate()([cnn.outputs[0], other_inputs.output])
    x = keras.layers.Dense(128, activation='relu')(x)
    x = keras.layers.Dense(64, activation='relu')(x)
    y = keras.layers.Dense(2, activation='sigmoid')(x)

    model = keras.Model([cnn.inputs[0], other_inputs.output], y)


    optimiser = keras.optimizers.Adam(lr)
    model.compile(optimizer=optimiser, loss='Huber', metrics=['MAE']+other_metrics)

    return model 

model = get_model()
model.summary()

2024-06-11 20:23:35.551733: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-06-11 20:23:35.583922: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-06-11 20:23:35.584160: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-

Model: "functional_2"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 64, 114,   │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling           │ (None, 64, 114,   │          0 │ input_layer[0][0] │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_translation  │ (None, 64, 114,   │          0 │ rescaling[0][0]   │
│ (RandomTranslation) │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_rotation     │ (None, 64, 114,   │          0 │ random_translati… │
│ (RandomRotation)    │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_zoom         │ (None, 64, 114,   │          0 │ random_rotation[… │
│ (RandomZoom)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_contrast     │ (None, 64, 114,   │          0 │ random_zoom[0][0] │
│ (RandomContrast)    │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_brightness   │ (None, 64, 114,   │          0 │ random_contrast[… │
│ (RandomBrightness)  │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d (Conv2D)     │ (None, 30, 55,    │      1,216 │ random_brightnes… │
│                     │ 16)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_1 (Conv2D)   │ (None, 13, 26,    │     12,832 │ conv2d[0][0]      │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_2 (Conv2D)   │ (None, 5, 11, 64) │     51,264 │ conv2d_1[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_3 (Conv2D)   │ (None, 3, 9, 64)  │     36,928 │ conv2d_2[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_4 (Conv2D)   │ (None, 1, 7, 96)  │     55,392 │ conv2d_3[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ flatten (Flatten)   │ (None, 672)       │          0 │ conv2d_4[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout (Dropout)   │ (None, 672)       │          0 │ flatten[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_1       │ (None, 4)         │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, 676)       │          0 │ dropout[0][0],    │
│ (Concatenate)       │                   │            │ input_layer_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 128)       │     86,656 │ concatenate[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_1 (Dense)     │ (None, 64)        │      8,256 │ dense[0][0]       │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_2 (Dense)     │ (None, 2)         │        130 │ dense_1[0][0]     │
└─────────────────────┴───────────────────┴────────────┴─────────────────

 Total params: 252,674 (987.01 KB)

 Trainable params: 252,674 (987.01 KB)

 Non-trainable params: 0 (0.00 B)

In [8]:
from train_tools import find_lr, tg_notify, use_tensorboard, end_epoch_notify

In [23]:
find_lr(get_model(), [train_frames, train_other], train_out)
#tensorboard --logdir src/training/logs --bind_all

Epoch 1/100


I0000 00:00:1718100759.303338  770111 service.cc:145] XLA service 0x7cfe8c0014c0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1718100759.303371  770111 service.cc:153]   StreamExecutor device (0): NVIDIA GeForce GTX 1650 SUPER, Compute Capability 7.5
2024-06-11 20:12:39.348068: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
2024-06-11 20:12:39.571917: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:465] Loaded cuDNN version 8907


 39/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1400 - loss: 0.0151

I0000 00:00:1718100764.204064  770111 device_compiler.h:188] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


342/342 ━━━━━━━━━━━━━━━━━━━━ 14s 24ms/step - MAE: 0.1375 - loss: 0.0147 - learning_rate: 1.0000e-06
Epoch 2/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1288 - loss: 0.0129 - learning_rate: 1.1220e-06
Epoch 3/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1188 - loss: 0.0111 - learning_rate: 1.2589e-06
Epoch 4/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1106 - loss: 0.0094 - learning_rate: 1.4125e-06
Epoch 5/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1077 - loss: 0.0088 - learning_rate: 1.5849e-06
Epoch 6/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1032 - loss: 0.0082 - learning_rate: 1.7783e-06
Epoch 7/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.0972 - loss: 0.0074 - learning_rate: 1.9953e-06
Epoch 8/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.0930 - loss: 0.0069 - learning_rate: 2.2387e-06
Epoch 9/100
342/342 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.0886 - loss: 0.0064 - learning_rate: 2.5119e-06
Epoch 10/100
342/342

In [9]:
model = get_model(2e-4)
model.fit(
    [train_frames, train_other],
    train_out,
    epochs=100, 
    validation_data = ([val_frames, val_other], val_out),
    callbacks=[
        tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10),
        use_tensorboard('training'), 
        end_epoch_notify()
        ] 
    )

Epoch 1/100


2024-06-11 20:23:45.451731: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:465] Loaded cuDNN version 8907


346/346 ━━━━━━━━━━━━━━━━━━━━ 7s 10ms/step - MAE: 0.1146 - loss: 0.0109 - val_MAE: 0.1454 - val_loss: 0.0139
Epoch 2/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 8ms/step - MAE: 0.0802 - loss: 0.0053 - val_MAE: 0.0541 - val_loss: 0.0030
Epoch 3/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 9ms/step - MAE: 0.0540 - loss: 0.0029 - val_MAE: 0.0534 - val_loss: 0.0030
Epoch 4/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 9ms/step - MAE: 0.0516 - loss: 0.0027 - val_MAE: 0.0523 - val_loss: 0.0028
Epoch 5/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 9ms/step - MAE: 0.0518 - loss: 0.0027 - val_MAE: 0.0525 - val_loss: 0.0029
Epoch 6/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 9ms/step - MAE: 0.0517 - loss: 0.0028 - val_MAE: 0.0525 - val_loss: 0.0028
Epoch 7/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 9ms/step - MAE: 0.0526 - loss: 0.0028 - val_MAE: 0.0521 - val_loss: 0.0028
Epoch 8/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 9ms/step - MAE: 0.0517 - loss: 0.0028 - val_MAE: 0.0524 - val_loss: 0.0029
Epoch 9/100
346/346 ━━━━━━━━━━━━━━━━━━━━ 3s 8ms/step - MAE:

In [ ]:
#frames_reindexed#, other_inputs_reindexed, outputs

# visualise the performance

In [10]:

#train_frames, train_other, train_out
val_idx = np.sort(val_idx)
train_idx = np.sort(train_idx)

val_y_pred = model.predict([frames_in[val_idx], other_in[val_idx]], batch_size=64)
train_y_pred = model.predict([frames_in[train_idx], other_in[train_idx]], batch_size=64)


val_out = out[val_idx]
train_out = out[train_idx]



42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step
173/173 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step


In [11]:
px.line(np.c_[train_out[:, :], train_y_pred[:, :]], title='train')

In [12]:
px.line(np.c_[val_out[:, :], val_y_pred[:, :]], title='val')